In [2]:
import pandas as pd
from functools import reduce
from tqdm import tqdm

import msgpack
import boto3
import awswrangler as wr
from io import BytesIO
import pickle
import numpy as np
import re
import datetime

import matplotlib.pyplot as plt
import seaborn as sns
import json

np.random.seed(1)

In [4]:
import warnings
warnings.filterwarnings("ignore")

# Connection

In [5]:
ACCESS_KEY='du3wAsX0uzEBBn4AdkFpCX4ZTXvSWFVG48GA4jbT'
SECRET_KEY='WA0NJOX0AFAY4K1J92XZ'

wr.config.s3_endpoint_url = 'https://obs.ru-moscow-1.hc.sbercloud.ru'

boto3.setup_default_session(
    region_name='ru-moscow',
    aws_access_key_id=SECRET_KEY,
    aws_secret_access_key=ACCESS_KEY,
)

def _get_default_boto3_client():
    return boto3.client('s3', endpoint_url=wr.config.s3_endpoint_url)

def get_object(s3_url):
    s3_client = _get_default_boto3_client()
    bucket, key = _split_3s_url_to_bucket_and_key(s3_url)
    return s3_client.get_object(Bucket=bucket, Key=key)


In [6]:
import pyspark
from pyspark.sql import SparkSession
import pyspark.sql.functions as F
from pyspark.sql.types import IntegerType
from pyspark.ml.feature import StringIndexer, IndexToString
from pyspark.ml import Pipeline
import pandas as pd
import numpy as np
from datetime import date
from scipy import sparse

spark = SparkSession.builder.appName("Dummy").master('local').config(
    "spark.driver.memory", "100g"
).config(
    "spark.driver.cores", '16'
).config(
    "spark.kryoserializer.buffer.max", '2047'
).getOrCreate()
print("session = ", spark.getActiveSession())
config_spark_s3_adv = {
    'access_id': 'WA0NJOX0AFAY4K1J92XZ',
    'access_key': 'du3wAsX0uzEBBn4AdkFpCX4ZTXvSWFVG48GA4jbT',
    'impl': 'org.apache.hadoop.fs.s3a.S3AFileSystem',
    'endpoint': 'https://obs.ru-moscow-1.hc.sbercloud.ru'
}

spark._jsc.hadoopConfiguration().set("fs.s3a.impl", config_spark_s3_adv["impl"])
spark._jsc.hadoopConfiguration().set("fs.s3a.endpoint", config_spark_s3_adv["endpoint"])
spark._jsc.hadoopConfiguration().set("fs.s3a.access.key", config_spark_s3_adv["access_id"])
spark._jsc.hadoopConfiguration().set("fs.s3a.secret.key", config_spark_s3_adv["access_key"])
spark._jsc.hadoopConfiguration().set("fs.s3a.aws.credentials.provider", "org.apache.hadoop.fs.s3a.SimpleAWSCredentialsProvider")
spark.sparkContext.uiWebUrl

22/11/17 12:50:58 WARN NativeCodeLoader: Unable to load native-hadoop library for your platform... using builtin-java classes where applicable
Using Spark's default log4j profile: org/apache/spark/log4j-defaults.properties
Setting default log level to "WARN".
To adjust logging level use sc.setLogLevel(newLevel). For SparkR, use setLogLevel(newLevel).


session =  <pyspark.sql.session.SparkSession object at 0x7fa55cfb6770>


'http://259bc79ca0eb:4040'

# Calculating

In [7]:
kp_path = 's3://ml-okko-object-storage/cold_start/data.json'
kp_df = wr.s3.read_json(kp_path).T

In [8]:
kp_df[kp_df['name_ru'].duplicated()]['name_ru'].value_counts()

Ералаш                    4
Близнецы                  3
В клетке                  3
Книга джунглей            3
Говорящий Том и друзья    3
                         ..
Обратная связь            1
Супергерои                1
Свинья                    1
Свингеры                  1
Бесконечная ночь          1
Name: name_ru, Length: 324, dtype: int64

In [9]:
data = pd.DataFrame(kp_df['description'])

In [10]:
data.isnull().sum()

description    255
dtype: int64

In [11]:
data

description
e785baa6-f175-42b4-9e16-4319ac7991d5  Кризис, разразившийся на песчаной планете Нимб...
4593737e-de9c-40df-97db-fb3cf85a08ef  После взрыва Праксиса, одной из лун Кроноса, у...
11ba66db-e941-4c3a-8da6-d8900e56f8c7  Неудачливый археолог возвращается из экспедици...
3f30a2ef-53b7-40e3-954f-1bdfc38a6d17  Эта «поджарка» была записана в Лос-Анджелесе 1...
cdfa700f-122d-41e5-b8dc-9c6813bab6d2                                               None
...                                                                                 ...
43bddcc0-db12-428e-9c65-f5606aa4b989  Рюрик, Александр Невский, Дмитрий Донской, Ива...
ac0c9152-c070-43a0-bb99-7e72764b7c0a                                               None
ce8d2906-a33f-4140-9ffe-e091990d71a4  После очередной травмы могулистка Молли Блум р...
0bfb5a13-50fc-48f3-b51a-a30971024651  Тысячи лет назад в древних историях осталось п...
6dd86e60-5d6d-475d-9b46-e989ac7a30b6  Цзян Цзыци — футболист из нашего времени, кото...

[10917 rows x 1 columns]

## Preprocessing

In [ ]:
!pip install razdel
!pip install pymystem3==0.1.10

In [63]:
data.dropna()[data.dropna().duplicated(keep=False)]

description
07b6d2a6-449e-4823-813f-4f1904085c0f  Адвокат Роберт Билотт выступает с обвинением в...
87b4a82f-d6db-4e07-bae2-d98f5c3b2a03  Чёрное сердце бьётся в груди молодого короля А...
481a5a96-c7a3-411d-a7dd-2deca5526b99  История Кенни Уэллса — современного золотоиска...
14e52eb8-cfd1-4391-b8b3-8638323dcc90  Молодой д’Артаньян покинул родной дом и отправ...
9057ccb5-2c91-4669-8575-2f644c7607e4  Эксцентричный мультимиллионер подписывает согл...
...                                                                                 ...
7becd8d8-1fb8-4ee6-b903-47817686ddd8  Генри страдает редким генетическим заболевание...
e6ea57ce-52eb-465b-b9b8-270bc498ca53  Чудом уцелев после падения с 20-го этажа, мене...
62541c49-7a32-45d0-8981-44ee6968d329  О борьбе за власть между двумя ветвями дома Та...
dd125e4d-8825-4c9b-8be4-4048f571aa92  1926 год. Разгар НЭПа. Новгородский жулик Подк...
ce8d2906-a33f-4140-9ffe-e091990d71a4  После очередной травмы могулистка Молли Блум р...

[241 rows x 1 columns]

In [ ]:
data.dropna()[data.dropna().duplicated(keep=False)].groupby('description').groups

In [ ]:
# '58ee7908-4c18-47d2-849e-5d45f32f3d38', '0a4d2ac4-6953-4c7f-8fbd-6be5e231fa5e' - эйфория 

In [ ]:
kp_df.loc['58ee7908-4c18-47d2-849e-5d45f32f3d38', :]

In [ ]:
kp_df.loc['0a4d2ac4-6953-4c7f-8fbd-6be5e231fa5e', :]

In [135]:
import re
from razdel import tokenize
from pymystem3 import Mystem
import nltk
from nltk.corpus import stopwords
nltk.download('stopwords')

ru_stopwords = set(stopwords.words('russian'))
ru_stopwords.add('это')
ru_stopwords.add('который')

class TextPreprocessing:
  def __init__(self, stopwords_removing=False, lemmatizing=False):
    self.stopwords_removing = stopwords_removing
    self.lemmatizing = lemmatizing
    
  def replace_backslash_n(self, texts):
    print(r'Replacing \n with whitespaces \\n...')
    pattern = re.compile('\.(\r|\n)')
    return [re.sub(pattern, '. ', text.strip()) for text in tqdm(texts)]

  def keep_cyrillic_only(self, texts):
    print('Keeping cyrillic only...')
    pattern = re.compile('[^А-Яа-яё ]')
    return [re.sub(pattern, '', text) for text in tqdm(texts)]

  def remove_backslash_n(self, texts):
    print(r'Removing \n...')
    pattern = re.compile('\n')
    return [re.sub(pattern, ' ', text.strip()) for text in tqdm(texts)]

  def tokenize(self, texts):
    print('Tokenizing...')
    return [[tokenized.text for tokenized in tokenize(text)] for text in tqdm(texts)]

  def lemmatize(self, texts):
    print('Lemmatizing...')
    lemmatizer = Mystem()
    return [''.join(lemmatizer.lemmatize(text)) for text in tqdm(texts)]

  def remove_stopwords(self, texts):
    print('Removing stopwords...')
    return [[w for w in text if w not in ru_stopwords] for text in tqdm(texts)]

  def transform(self, texts):
    texts = texts.map(lambda x: x.replace(u'\xa0', ' '))
    texts = self.replace_backslash_n(texts)
    texts = self.keep_cyrillic_only(texts)
    texts = [text.lower() for text in texts]

    if self.lemmatizing:
        texts = self.lemmatize(texts)
    
    texts = self.tokenize(texts)
    
    if self.stopwords_removing:
        texts = self.remove_stopwords(texts)

    return texts

[nltk_data] Downloading package stopwords to /home/jovyan/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


In [103]:
df = data.dropna()
df.reset_index(drop=True, inplace=True)
preprocesser = TextPreprocessing(stopwords_removing=True, lemmatizing=True)

df_pr = preprocesser.transform(df['description'])
tokens = reduce(lambda x, y : x + y, df_pr)

Replacing 
 with whitespaces \n...


100% 10662/10662 [00:00<00:00, 262987.26it/s]


Keeping cyrillic only...


100% 10662/10662 [00:00<00:00, 112922.47it/s]


Lemmatizing...


100% 10662/10662 [00:23<00:00, 446.71it/s]


Tokenizing...


100% 10662/10662 [00:02<00:00, 3615.43it/s]


Removing stopwords...


100% 10662/10662 [00:00<00:00, 115019.73it/s]


In [104]:
df_pr[0]

['кризис',
 'разражаться',
 'песчаный',
 'планета',
 'нимбус',
 'располагать',
 'нейтральный',
 'зона',
 'казаться',
 'лишь',
 'акт',
 'заявление',
 'местный',
 'бунтарство',
 'желающий',
 'лишь',
 'привлекать',
 'внимание',
 'федерация',
 'повстанец',
 'лидер',
 'уроженец',
 'планета',
 'вулкан',
 'имя',
 'сайбок',
 'обладать',
 'выдающийся',
 'вулканеанский',
 'мерка',
 'парапсихологический',
 'способность',
 'достаточно',
 'лишь',
 'краткий',
 'общение',
 'человек',
 'либо',
 'инопланетянин',
 'испытывать',
 'чувство',
 'безраздельный',
 'доверие',
 'сайбок',
 'объявлять',
 'новый',
 'мессия',
 'собираться',
 'отправляться',
 'поиск',
 'думать',
 'бог',
 'некстати',
 'подвертываться',
 'рука',
 'энтерпрайз',
 'свой',
 'команда',
 'вынуждать',
 'выполнять',
 'данный',
 'миссия',
 'спока',
 'немногие',
 'поддавшисеться',
 'внушение',
 'мочь',
 'подымать',
 'рука',
 'свой',
 'родной',
 'брат',
 'путь',
 'лежать',
 'центр',
 'галактика',
 'великий',
 'барьер',
 'таинственный',
 'планета

In [105]:
df['description'][0]

'Кризис, разразившийся на песчаной планете Нимбус III (Nimbus III), расположенной в нейтральной зоне, казалось бы, был всего лишь еще одним актом заявления о себе местного бунтарства, желающем лишь привлечь внимание Федерации - но не на этот раз.\n\nТеперь у повстанцев есть лидер, уроженец планеты Вулкан по имени Сайбок (Sybok), обладающий выдающимися даже по вулканеанским меркам парапсихологическими способностями - ему достаточно лишь краткого общения для того, чтобы человек либо другой инопланетянин испытывал к нему чувство безраздельного доверия.\n\nСайбок объявляет себя новым мессией и собирается отправиться на поиски - кого бы вы думали? - Бога! И некстати подвернувшийся ему под руку «Энтерпрайз» со своей командой будет вынужден выполнить данную миссию, ведь даже Спок, один из немногих не поддавшися внушению, не может поднять руку на своего... родного брата.\r\n\r\nИх путь лежит в центр галактики, за Великий Барьер (The Great Barrier), на таинственную планету Ша Ка Ри (Sha Ka Ree)

In [108]:
pd.Series(tokens).value_counts()

свой              5464
жизнь             3401
друг              2594
год               2512
весь              2478
                  ... 
хипстерский          1
грузиться            1
транссибирский       1
царапать             1
цзися                1
Length: 33832, dtype: int64

## N-grams TBD

In [109]:
def create_n_grams(texts, n=2):
  n_grams = []

  for text in texts:
    text_n_grams = []
    for i in range(len(text)-n):
      text_n_grams.append(' ' .join(text[i:i+n]))
    n_grams.append(text_n_grams)
  return n_grams

In [110]:
# preprocesser = TextPreprocessing(stopwords_removing=False, lemmatizing=True)

# data_for_n_grams = preprocesser.transform(data.dropna()['description'])

bigrams = create_n_grams(df_pr)
bigrams = reduce(lambda x, y : x + y, bigrams)

## Refference corpus

In [111]:
from bs4 import BeautifulSoup 
import glob
from random import choices
import random
import re

random.seed(123)

In [112]:
def get_freq(text, n=1, voc=None):
  if voc is None:
    voc = set(text)
  word_freq = {}
  for word in tqdm(text):
    word_freq[word] = word_freq.get(word, n) + 1

  return word_freq

In [114]:
files = [f for f in glob.glob("/home/jovyan/work/data/xmls/*.xml")]
print(f'Number of files {len(files)}')

Number of files 4007


In [115]:
files = choices(files, k=1000)

In [128]:
# Reading the data inside the xml file to a variable under the name  data
data_oc = []
for file in files:
  with open(f'{file}', 'r') as f:
      file = f.read()
      bs_data = BeautifulSoup(file, 'xml')
      data_oc.append(bs_data.find_all('source'))

In [129]:
data_oc

[[<source>Работко</source>,
  <source>Вчера был замечательный рабочий день.</source>,
  <source>Мы молодежным коллективом в свободное время загадывали и обсуждали различные интересные задачки.</source>,
  <source>Задача 1.</source>,
  <source>Перед вами стоят три ширмы.</source>,
  <source>За двумя из них по козлу, за третьей машина, которую вы хотите выиграть.</source>,
  <source>Вы выбираете ширму, а ведущий открывает ширму, отличную от выбранной, за которой стоит козел.</source>,
  <source>Далее вам дается право поменять выбранную ширму.</source>,
  <source>После чего вы забираете свой приз.</source>,
  <source>Вопрос: стоит ли пользоваться этим правом?</source>,
  <source>Задача 2.</source>,
  <source>Перед вами стоят три корзины.</source>,
  <source>В одной яблоки, во другой апельсины, в третьей яблоки с апельсинами.</source>,
  <source>Вы не видите что в какой корзине находится.</source>,
  <source>Однако знаете, надписи, указывающие где что лежит, на корзинах перепутаны.</source

In [130]:
pattern = re.compile('</?source>')
data_oc_series = pd.Series([re.sub(pattern, '', str(sent)) for text in data_oc for sent in text])

In [138]:
preprocesser = TextPreprocessing(stopwords_removing=True, lemmatizing=True)

data_oc_norm = preprocesser.transform(data_oc_series)

Работко
Replacing 
 with whitespaces \n...


100% 27704/27704 [00:00<00:00, 346281.75it/s]


Работко
Keeping cyrillic only...


100% 27704/27704 [00:00<00:00, 203088.65it/s]


Работко
работко
Lemmatizing...


...

работко

Tokenizing...


100% 27704/27704 [00:01<00:00, 14585.46it/s]


['работко']
Removing stopwords...


100% 27704/27704 [00:00<00:00, 456622.45it/s]

['работко']


In [140]:
# 553 sec
data_oc_norm = reduce(lambda x, y : x + y, data_oc_norm)

In [141]:
data_oc_norm

['работко',
 'вчера',
 'замечательный',
 'рабочий',
 'день',
 'молодежный',
 'коллектив',
 'свободный',
 'время',
 'загадывать',
 'обсуждать',
 'различный',
 'интересный',
 'задачка',
 'задача',
 'стоять',
 'ширма',
 'козел',
 'третий',
 'машина',
 'хотеть',
 'выигрывать',
 'выбирать',
 'ширма',
 'ведущий',
 'открывать',
 'ширма',
 'отличный',
 'выбирать',
 'стоять',
 'козел',
 'далее',
 'даваться',
 'право',
 'поменять',
 'выбирать',
 'ширма',
 'забирать',
 'свой',
 'приз',
 'вопрос',
 'стоять',
 'пользоваться',
 'право',
 'задача',
 'стоять',
 'корзина',
 'яблоко',
 'апельсин',
 'третий',
 'яблоко',
 'апельсин',
 'видеть',
 'корзина',
 'находиться',
 'однако',
 'знать',
 'надпись',
 'указывать',
 'лежать',
 'корзина',
 'перепутывать',
 'даваться',
 'право',
 'вытягивать',
 'любой',
 'корзина',
 'фрукт',
 'взглядывать',
 'корректно',
 'расставлять',
 'надпись',
 'задача',
 'домик',
 'гном',
 'ворваться',
 'тролль',
 'решать',
 'сжирать',
 'гном',
 'взмаливаться',
 'крайний',
 'мера',


In [142]:
len(data_oc_norm)

264856

## Get frequencies, calculate ratio

In [143]:
frec_oc = get_freq(data_oc_norm)

100% 264856/264856 [00:00<00:00, 2404079.30it/s]


In [144]:
frec_oc_list = [(k, v) for k, v in frec_oc.items()]
frec_oc_list.sort(key=lambda x: x[1])
frec_oc_list[-20:]

[('иметь', 464),
 ('работа', 468),
 ('дело', 481),
 ('говорить', 484),
 ('день', 488),
 ('являться', 542),
 ('российский', 555),
 ('место', 560),
 ('россия', 564),
 ('самый', 606),
 ('новый', 608),
 ('первый', 609),
 ('становиться', 788),
 ('также', 791),
 ('время', 960),
 ('человек', 1141),
 ('мочь', 1159),
 ('весь', 1272),
 ('свой', 1531),
 ('год', 2165)]

In [145]:
frec_data = get_freq(tokens)

100% 418321/418321 [00:00<00:00, 2416577.06it/s]


In [146]:
frec_data_list = [(k, v) for k, v in frec_data.items()]
frec_data_list.sort(key=lambda x: x[1])
frec_data_list[-20:]

[('семья', 1190),
 ('жить', 1194),
 ('молодой', 1270),
 ('находить', 1293),
 ('мочь', 1309),
 ('решать', 1320),
 ('история', 1401),
 ('оказываться', 1414),
 ('девушка', 1451),
 ('мир', 1643),
 ('самый', 1650),
 ('новый', 1685),
 ('время', 1725),
 ('человек', 2106),
 ('становиться', 2229),
 ('весь', 2479),
 ('год', 2513),
 ('друг', 2595),
 ('жизнь', 3402),
 ('свой', 5465)]

In [147]:
word_spec = {}

for word, freq in frec_data.items():
  word_spec[word] = freq / frec_oc.get(word, 1)

In [148]:
word_spec_list = [(k, v) for k, v in word_spec.items()]
word_spec_list.sort(key=lambda x: x[1], reverse=True)

In [149]:
pd.DataFrame(word_spec_list, columns=['Word', 'freq_rusentiment / freq_opencorpora']).head(20)# .to_csv('/content/sample_data/keywords_from_frequency.csv')

Word  freq_rusentiment / freq_opencorpora
0     ограбление                                118.0
1           макс                                115.0
2       отважный                                113.0
3     супергерой                                 87.0
4         маньяк                                 86.0
5      одержимый                                 83.0
6        мечтать                                 75.5
7           джек                                 73.5
8          побег                                 73.0
9        подруга                                 72.0
10       парочка                                 67.0
11           сэм                                 67.0
12          даша                                 66.0
13  расследовать                                 64.5
14       призрак                                 63.0
15         дэнни                                 63.0
16       наемный                                 60.0
17        киллер                                 60.0
18   бесстрашный                                 59.0
19      гангстер                                 58.0

In [156]:
keywords = pd.DataFrame(word_spec_list, columns=['token', 'freq_ratio'])

In [157]:
keywords.to_csv('keywords.csv')

# Encoding TBD

In [ ]:
# def encode_keywords(texts, kw):
#     preprocesser = TextPreprocessing(stopwords_removing=True, lemmatizing=True)
#     texts = preprocesser.transform(texts.dropna())
#     keywords = pd.DataFrame(np.full((len(texts), len(kw)), 0), columns=kw['token'])
#     keywords['texts'] = texts
    
#     for i, text in texts:
#         for token in text:
#             keywords.loc[i, token] = 1
            
#     return keywords